[View in Colaboratory](https://colab.research.google.com/github/NagrajN/tensorflow/blob/master/HW9Part1.ipynb)

In [0]:
import os
import requests
import shutil
import subprocess
import tensorflow as tf

__all__ = [
  'install_ngrok', 
  'launch_tensorboard',
]

def __shell__(cmd, split=True):
  # get_ipython().system_raw(cmd)
  result = get_ipython().getoutput(cmd, split=split)
  if result and not split:
    result = result.strip('\n')
  return result  


# tested OK
def install_ngrok(bin_dir="/tmp"):
  """ download and install ngrok on local vm instance
  Args:
    bin_dir: full path for the target directory for the `ngrok` binary
  """
  TARGET_DIR = bin_dir
  CWD = os.getcwd()
  is_grok_avail = os.path.isfile(os.path.join(TARGET_DIR,'ngrok'))
  if is_grok_avail:
    print("ngrok installed")
  else:
    import platform
    plat = platform.platform() # 'Linux-4.4.64+-x86_64-with-Ubuntu-17.10-artful'
    if 'x86_64' in plat:
      
      os.chdir('/tmp')
      print("calling wget https://bin.equinox.io/c/4VmDzA7iaHb/ngrok-stable-linux-amd64.zip ..." )
      get_ipython().system_raw( "wget https://bin.equinox.io/c/4VmDzA7iaHb/ngrok-stable-linux-amd64.zip" )
      print("calling unzip ngrok-stable-linux-amd64.zip ...")
      get_ipython().system_raw( "unzip ngrok-stable-linux-amd64.zip" )
      os.rename("ngrok", "{}/ngrok".format(TARGET_DIR))
      os.remove("ngrok-stable-linux-amd64.zip")
      is_grok_avail = os.path.isfile(os.path.join(TARGET_DIR,'ngrok'))
      os.chdir(TARGET_DIR)
      if is_grok_avail:
        print("ngrok installed. path={}".format(os.path.join(TARGET_DIR,'ngrok')))
      else:
        # ValueError: ERROR: ngrok not found, path=
        raise ValueError( "ERROR: ngrok not found, path=".format(TARGET_DIR) )
    else:
      raise NotImplementedError( "ERROR, ngrok install not configured for this platform, platform={}".format(plat))
    os.chdir(CWD)
    return
    
# tested OK
def launch_tensorboard(bin_dir="/tmp", log_dir="/tmp", retval=False):
  """returns a public tensorboard url based on the ngrok package
  checks if `ngrok` is available, and installs, if necessary, to `bin_dir`
  launches tensorboard, if necessary
  see: https://stackoverflow.com/questions/47818822/can-i-use-tensorboard-with-google-colab
  Args:
    bin_dir: full path for the target directory for the `ngrok` binary
    log_dir: full path for the tensorflow `log_dir`
  Return:
    public url for tensorboard if retval==True
      NOTE: the method will print a link to stdout (cell output) for the tensorflow URL. 
      But the link printed from the return value has an extra "%27" in the URL which causes an error
  """
  install_ngrok(bin_dir)
    
  if not tf.gfile.Exists(log_dir):  tf.gfile.MakeDirs(log_dir)
  
  # check status of tensorboard and ngrok
  ps = __shell__("ps -ax")
  is_tensorboard_running = len([f for f in ps if "tensorboard" in f ]) > 0
  is_ngrok_running = len([f for f in ps if "ngrok" in f ]) > 0
  print("status: tensorboard={}, ngrok={}".format(is_tensorboard_running, is_ngrok_running))

  if not is_tensorboard_running:
    get_ipython().system_raw(
        'tensorboard --logdir {} --host 0.0.0.0 --port 6006 &'
        .format(log_dir)
    )
    is_tensorboard_running = True
    
  if not is_ngrok_running:  
    #    grok should be installed in /tmp/ngrok
    get_ipython().system_raw('{}/ngrok http 6006 &'.format(bin_dir))
    is_ngrok_running = True

  # get tensorboard url
  # BUG: getting connection refused for HTTPConnectionPool(host='localhost', port=4040)
  #     on first run, retry works
  import time
  time.sleep(3)
  retval = requests.get('http://localhost:4040/api/tunnels')
  tensorboard_url = retval.json()['tunnels'][0]['public_url'].strip()
  print("tensorboard url=", tensorboard_url)
  if retval:
    return tensorboard_url

In [0]:
import shutil

try:
  shutil.rmtree('/content/log')
except:
  pass

In [6]:
ROOT = %pwd
print(ROOT)


LOG_DIR = os.path.join(ROOT, 'log')

# will install `ngrok`, if necessary
# will create `log_dir` if path does not exist
launch_tensorboard( bin_dir=ROOT, log_dir=LOG_DIR )

/content
ngrok installed
status: tensorboard=True, ngrok=True
tensorboard url= http://c5e8d429.ngrok.io


'http://c5e8d429.ngrok.io'

In [0]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
  loss_var = tf.summary.scalar('loss', loss)

  # Calculate Accuracy
  _ , accuracy = tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])
  accuracy_var = tf.summary.scalar('accuracy', accuracy)
  
  summary_hook_steps = 100
  
  summary_hook_train = tf.train.SummarySaverHook(
    
    summary_hook_steps,
    output_dir= '/content/log/mnist/modified/1/train',    
    summary_op = tf.summary.merge_all()
  )
  
  
  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op, training_hooks=[summary_hook_train])

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)





In [8]:
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=50000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      steps=500,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  #print(eval_results)


Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_ch

INFO:tensorflow:global_step/sec: 74.4572
INFO:tensorflow:probabilities = [[0.00020714 0.00000306 0.00003744 0.00016856 0.00101931 0.00002399
  0.00000276 0.00114717 0.00017933 0.99721116]
 [0.00000014 0.00000027 0.00000213 0.00000288 0.999094   0.00000014
  0.00000218 0.0000131  0.00000841 0.00087676]
 [0.00000045 0.00000577 0.00000856 0.00007388 0.99126875 0.00001545
  0.00000165 0.00056199 0.00012613 0.00793731]
 [0.00194948 0.00303116 0.00297273 0.07589675 0.00033044 0.09307566
  0.00016898 0.00016736 0.8210338  0.00137372]
 [0.00001238 0.99729854 0.00025027 0.00082622 0.00015406 0.00009399
  0.00031093 0.00010509 0.0008673  0.00008115]
 [0.00000242 0.00000001 0.00000037 0.00000116 0.00001795 0.00002002
  0.00001175 0.00000011 0.9998598  0.00008647]
 [0.00000001 0.00000001 0.00000284 0.00003414 0.00000001 0.00000039
  0.         0.9999449  0.0000001  0.00001767]
 [0.00000005 0.0009503  0.9963664  0.00266944 0.         0.00000275
  0.00000059 0.00000249 0.00000802 0.        ]
 [0.000

INFO:tensorflow:probabilities = [[0.00626336 0.00504521 0.0032484  0.02135138 0.00000937 0.00022552
  0.00001908 0.01893993 0.9390274  0.00587033]
 [0.00134623 0.00005117 0.00027753 0.05111661 0.00020621 0.9441169
  0.00005538 0.00016379 0.00086692 0.00179938]
 [0.00001388 0.00052862 0.00001906 0.00002375 0.9562581  0.00019536
  0.0000147  0.0008469  0.00096199 0.0411376 ]
 [0.00000411 0.00000134 0.00000149 0.00000032 0.9995105  0.00000777
  0.00002542 0.0000125  0.00000269 0.00043392]
 [0.00000569 0.00013181 0.00113735 0.9829457  0.00000168 0.00979458
  0.00000005 0.00003559 0.00574045 0.00020713]
 [0.00000037 0.00002568 0.00064916 0.9992094  0.00000002 0.00002953
  0.00000005 0.0000001  0.00008503 0.00000057]
 [0.0096422  0.00493386 0.00007488 0.00097463 0.00225211 0.00589787
  0.96040374 0.00000627 0.01579102 0.00002337]
 [0.0162497  0.00008767 0.26697838 0.40377477 0.00009257 0.00184659
  0.00165862 0.08860414 0.19379237 0.02691516]
 [0.00079789 0.00049539 0.00002638 0.00018469 0.0

INFO:tensorflow:probabilities = [[0.00005224 0.00155021 0.00152241 0.0001615  0.96556115 0.00024156
  0.01113391 0.00074407 0.00845613 0.0105767 ]
 [0.00000027 0.00000019 0.00032283 0.9996184  0.         0.00000227
  0.         0.00000003 0.00005285 0.00000312]
 [0.27653122 0.01169329 0.0061241  0.2505694  0.00827728 0.01148065
  0.06526819 0.00034766 0.3617208  0.00798737]
 [0.00000241 0.00008376 0.01310668 0.00243019 0.00087163 0.00000688
  0.00001042 0.983055   0.00005553 0.00037732]
 [0.00038712 0.00030285 0.00195387 0.0001988  0.98656183 0.00056007
  0.00701997 0.00042896 0.00099019 0.00159635]
 [0.9999478  0.00000001 0.00000882 0.00000099 0.         0.00003811
  0.00000003 0.0000035  0.00000006 0.00000082]
 [0.00000005 0.00000812 0.00004074 0.9997843  0.         0.00000923
  0.         0.00000185 0.00011354 0.00004215]
 [0.000806   0.00264419 0.01287688 0.95054454 0.00158562 0.01460125
  0.00050132 0.00008814 0.01329192 0.00306014]
 [0.00020986 0.99601656 0.00045436 0.00010197 0.

INFO:tensorflow:probabilities = [[0.00009768 0.00007414 0.00001122 0.00122991 0.0000085  0.9972132
  0.00003247 0.00001438 0.00127508 0.00004336]
 [0.99086106 0.0000023  0.00013251 0.00001484 0.00000337 0.0046415
  0.00144896 0.00000466 0.00212941 0.00076147]
 [0.00002278 0.00000001 0.00000741 0.00000001 0.00000348 0.00030076
  0.9996377  0.         0.00002774 0.00000003]
 [0.00016008 0.00005901 0.00023521 0.00185761 0.0003759  0.95453596
  0.03112251 0.00000148 0.01138241 0.00026995]
 [0.0001684  0.00078847 0.00009932 0.00000971 0.9797332  0.0005528
  0.00046716 0.01020472 0.00356469 0.00441154]
 [0.00000053 0.00009016 0.8859732  0.00026438 0.00028747 0.00000847
  0.00006559 0.11326184 0.00001822 0.00003019]
 [0.00001739 0.00000095 0.00032847 0.00020937 0.00220252 0.00000343
  0.00000328 0.00321752 0.00321346 0.9908036 ]
 [0.00000451 0.00002461 0.00005659 0.12883484 0.00001179 0.68115455
  0.00000024 0.00099114 0.02754629 0.1613754 ]
 [0.00000002 0.00000465 0.00004313 0.9998685  0.000

...

INFO:tensorflow:probabilities = [[0.00000113 0.00000041 0.00005119 0.00000027 0.9999064  0.00000177
  0.00001932 0.00000577 0.00000134 0.00001225]
 [0.00018162 0.00077688 0.00050751 0.00016318 0.00018954 0.00216724
  0.00000703 0.00166891 0.99252105 0.00181708]
 [0.00072234 0.0000231  0.00006356 0.00234585 0.00000162 0.00208617
  0.00000627 0.00000229 0.99456716 0.00018163]
 [0.00000018 0.00000103 0.00003529 0.9999256  0.00000001 0.00001471
  0.         0.00000007 0.00000512 0.000018  ]
 [0.00000003 0.00000349 0.99837387 0.00061912 0.00000003 0.00087879
  0.00000006 0.00009193 0.00002606 0.00000649]
 [0.00000019 0.00000006 0.00000002 0.00000947 0.00011459 0.00000005
  0.         0.00353356 0.00000011 0.9963419 ]
 [0.00017035 0.00258618 0.00058529 0.0027778  0.00000116 0.00000133
  0.         0.9883758  0.00019467 0.00530743]
 [0.         0.         0.         0.00067352 0.         0.99926716
  0.         0.         0.0000002  0.00005911]
 [0.00000001 0.         0.00000011 0.00009105 0.

INFO:tensorflow:probabilities = [[0.99999344 0.00000016 0.00000346 0.00000004 0.00000019 0.0000008
  0.00000093 0.00000008 0.00000001 0.00000092]
 [0.00001329 0.9991917  0.00023106 0.00001954 0.0000957  0.00000026
  0.0000289  0.00032152 0.00009491 0.00000306]
 [0.00005378 0.0002057  0.00003468 0.00609047 0.00000532 0.84499174
  0.14461634 0.00000006 0.00393954 0.0000624 ]
 [0.00000274 0.00016166 0.00028499 0.9849224  0.00000105 0.00003158
  0.00000002 0.00002049 0.00381582 0.01075925]
 [0.00000007 0.         0.00000815 0.00000041 0.00000006 0.00000059
  0.         0.9997458  0.         0.000245  ]
 [0.00000107 0.9996357  0.00000544 0.0001619  0.00006026 0.00000025
  0.00001018 0.00005816 0.00003175 0.0000353 ]
 [0.00027608 0.00006396 0.00085808 0.07663273 0.00167613 0.6652292
  0.00138862 0.00036683 0.15643875 0.0970697 ]
 [0.00000673 0.00000187 0.0000001  0.00000001 0.00001417 0.00000435
  0.99997115 0.         0.00000164 0.00000002]
 [0.00000008 0.00000002 0.00000232 0.0004406  0.00

INFO:tensorflow:probabilities = [[0.0000026  0.00000006 0.9926351  0.00686512 0.00000015 0.00000291
  0.00000003 0.00048906 0.00000311 0.00000198]
 [0.00000517 0.99915266 0.00029198 0.00000427 0.00011577 0.00000202
  0.00003736 0.0000726  0.00031742 0.00000083]
 [0.00004753 0.00000003 0.00002172 0.00000085 0.00000544 0.00058927
  0.9993253  0.         0.00000914 0.00000071]
 [0.00000052 0.00000001 0.00000051 0.00000001 0.00000245 0.00004765
  0.9999429  0.         0.00000593 0.00000003]
 [0.00000292 0.00001734 0.00000023 0.00018797 0.00000003 0.99970263
  0.00000069 0.00000076 0.00002522 0.00006226]
 [0.00000006 0.00000008 0.00010972 0.00001033 0.         0.00000001
  0.         0.9998766  0.00000003 0.00000322]
 [0.0000003  0.00065482 0.00001883 0.9764647  0.00000002 0.02284276
  0.00000005 0.00000012 0.00001817 0.00000027]
 [0.00000234 0.99925846 0.00009226 0.00000444 0.00021582 0.00000004
  0.00003169 0.00032788 0.00006472 0.00000225]
 [0.00000267 0.0000004  0.00000004 0.00099883 0.

INFO:tensorflow:probabilities = [[0.00000168 0.99821377 0.00169887 0.00000114 0.00001252 0.00000003
  0.00000328 0.00003697 0.00003026 0.00000158]
 [0.0000107  0.9980438  0.00015477 0.00000676 0.00018919 0.00000049
  0.00000338 0.00152139 0.00004855 0.00002093]
 [0.00052366 0.00037112 0.07318243 0.89376885 0.00024135 0.00343414
  0.00014501 0.00002485 0.02332718 0.00498143]
 [0.00000023 0.00000004 0.00000064 0.00002759 0.00002885 0.0000017
  0.         0.00000516 0.0000238  0.9999119 ]
 [0.         0.00000002 0.00000001 0.00287854 0.         0.9964893
  0.         0.0000049  0.00000438 0.00062296]
 [0.0003332  0.00182232 0.00235697 0.04161168 0.00000082 0.9527767
  0.00000548 0.00002575 0.00075367 0.00031344]
 [0.00000077 0.00000893 0.00009733 0.00012558 0.00000002 0.00000001
  0.         0.99926144 0.00000372 0.00050216]
 [0.00000114 0.00019853 0.9951369  0.00039411 0.00160575 0.0007585
  0.00005224 0.00184989 0.00000164 0.00000137]
 [0.00041046 0.00006653 0.9883956  0.00412127 0.0003

KeyboardInterrupt: ignored